In [1]:
# Inicialization

from __future__ import print_function
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
from urllib.request import urlopen
import os
from IPython import get_ipython
import string
import sys
from pylab import *
from itertools import combinations_with_replacement



def is_interactive(): # are we in jupyter ??
    import __main__ as main
    return 0 


#if is_interactive():
#    %matplotlib inline

#Experimental setup
ShotNo=26789
Signals=['drp2','drp4','drp6','drp8']
#Signals=['drp2','drp4'] #testit
step=500 # us
#step=5000 # test



HWNapetovyDelic=100 


#Global variables
PlasmaStart=0
PlasmaEnd=0
# correlation setup
# graph setup
GV_BottomGraphLimit=0.0;GV_zoomexrange=0.1

BaseURL = "http://golem.fjfi.cvut.cz/utils/data/" #global


FigSize=10,8
def FigDef():plt.figure(figsize=(10, 8), dpi= 80, facecolor='w', edgecolor='k')

#print(list(combinations_with_replacement(Signals, 2)))
 

In [2]:
# Functions definitions
def mkdir(dir):  
    try:os.makedirs(dir) 
    except OSError:pass
    

def GMgetdata_npz(ShotNo, signal):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/'+signal+'.npz'):
        os.system('wget http://golem.fjfi.cvut.cz/shots/' + str(ShotNo) + '/basicdiagn/'+signal+'.npz -O Data/'+signal+'.npz');
    

def GMgetfigure(ShotNo, identification):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/graphres.png'):
        os.system('wget http://golem.fjfi.cvut.cz/shots/' + ShotNoStr + '/basicdiagn/graphpres.png -O Data/graphres.png');
 
    
def GMgetdata_txt(ShotNo, signal):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/'+signal+'.txt'):
        os.system('wget http://golem.fjfi.cvut.cz/utils/data/' + ShotNoStr + '/'+signal+'.txt -O Data/'+signal+'.txt');
    return np.loadtxt('Data/'+signal+'.txt')[PlasmaStart:PlasmaEnd]    

def GMgetdata_identifier(ShotNo, signal):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/'+signal):
        os.system('wget http://golem.fjfi.cvut.cz/utils/data/' + ShotNoStr + '/'+signal+' -O Data/'+signal);
    return np.loadtxt('Data/'+signal)
        
def GMgetparameter(ShotNo,identifier):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/'+identifier):
        parameter=str(urlopen(BaseURL+str(ShotNo)+'/'+identifier).read().rstrip()).replace("b'", "").replace("'","")
        np.savetxt('Data/'+identifier,[parameter], delimiter=" ", fmt="%s")
        return parameter
    return np.loadtxt('Data/'+identifier)

def GMget_str_parameter(ShotNo,identifier):
    ShotNoStr=str(ShotNo)
    if not os.path.isfile('Data/'+identifier):
        parameter=str(urlopen(BaseURL+str(ShotNo)+'/'+identifier).read().rstrip()).replace("b'", "").replace("'","")
        np.savetxt('Data/'+identifier,[parameter], delimiter=" ", fmt="%s")
        return parameter
    return open('Data/'+identifier, 'r').read()




def GetData(ShotNo):
    global PlasmaStart
    global PlasmaEnd
    mkdir('Data')
    mkdir('CrossCorrels')
    ShotNoStr=str(ShotNo)
    GMgetdata_npz(ShotNo, "Btoroidal")
    GMgetfigure(ShotNo,'graphres.png')
    #Plasma parameters
    PlasmaStart=int(float(GMgetparameter(ShotNo,'plasma_start'))*1e6) # in us
    PlasmaEnd=int(float(GMgetparameter(ShotNo,'plasma_end'))*1e6) # in us
    
     
def DischargeBasics(ShotNo,VacuumShot,PlasmaStart, PlasmaEnd, Time, Uloop, Btoroidal, Iplasma, \
                    VAchar_voltage, VAchar_current,Potential, Potential_smoothed, dz):
    
    f = plt.figure(figsize=(20.0, 5.0))
    f,ax = plt.subplots(3,sharex=True);plt.subplots_adjust(hspace=0.001)
    f.set_size_inches(FigSize)
    ax[0].set_title('#' + str(ShotNo))
    ax[0].plot(Time/1000,Uloop['data'][PlasmaStart:PlasmaEnd],label='Loop voltage');ax[0].set_ylabel('$U_l$ [V]');ax[0].set_ylim(0,);ax[0].legend(loc=0)
    ax[1].plot(Time/1000,Btoroidal['data'][PlasmaStart:PlasmaEnd],label='Toroidal magnetic field');ax[1].set_ylabel('$B_t$ [T]');ax[1].set_ylim(0,);ax[1].legend(loc=0)
    ax[2].plot(Time/1000,Iplasma['data'][PlasmaStart:PlasmaEnd]/1000,label='Plasma current');ax[2].set_ylabel('$I_p$ [kA]');ax[2].set_ylim(0,);ax[2].legend(loc=0)
    ax[2].set_xlabel('$t$ [ms]');#ax[6].set_ylim(-200,200)
    ax[2].set_xlim(PlasmaStart/1000,PlasmaEnd/1000)
    plt.savefig('/Basics/BasicDiag.jpg', bbox_inches='tight')
    if is_interactive():plt.show();
    plt.close();
    

    
def GMcrosscorrelation(ShotNo,signal1,signal2,start_time, end_time):
    a_array=GMgetdata_txt(ShotNo, signal1)[start_time:end_time][0:,1]
    v_array=GMgetdata_txt(ShotNo, signal2)[start_time:end_time][0:,1]
    plt.clf();plt.plot(a_array,label=signal1);plt.plot(v_array,label=signal2);
    plt.legend(loc=1)
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+'raw.jpg', bbox_inches='tight')
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+signal1+'raw.dat',[a_array], delimiter="\n", fmt="%s")
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+signal2+'raw.dat',[v_array], delimiter="\n", fmt="%s")
    plt.clf();plt.plot(a_array-np.mean(a_array),label=signal1);plt.plot(v_array-np.mean(v_array),label=signal2);
    plt.legend(loc=1)
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+'raw-mean.jpg', bbox_inches='tight')
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+signal1+'raw-mean.dat',[a_array], delimiter="\n", fmt="%s")
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+signal2+'raw-mean.dat',[v_array], delimiter="\n", fmt="%s")
    # priprava normalizace
    a_array = (a_array - np.mean(a_array)) / (np.std(a_array) * len(a_array))
    v_array = (v_array - np.mean(v_array)) / (np.std(v_array))
    correlation=np.correlate(a_array, v_array, mode='full')
    plt.clf()
    plt.plot(correlation)
    plt.axis([0,2*len(a_array),-1,1])
    plt.title('#'+str(ShotNo)+' Cross-correlation '+signal1+' x '+signal2+' <'+str(start_time)+','+str(end_time)+ '>us')
    plt.grid()
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+'.jpg', bbox_inches='tight')
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+'.dat',[correlation], delimiter="\n", fmt="%s")
    plt.clf()
    #plt.show()
    plt.plot(correlation)
    plt.title('#'+str(ShotNo)+' Cross-correlation '+signal1+' x '+signal2+' <'+str(start_time)+','+str(end_time)+ '>us zoom')
    plt.axis([len(a_array)*(1-GV_zoomexrange),len(a_array)*(1+GV_zoomexrange) , GV_BottomGraphLimit,1])
    plt.axvline(x=np.argmax(correlation),color='k', linestyle='--')
    plt.grid()
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/'+str(start_time)+'to'+str(end_time)+'z.jpg', bbox_inches='tight')
    #if is_interactive():plt.show();
    #plt.show();    
    return np.argmax(correlation)+1,correlation[np.argmax(correlation)+1]
 
    
#GMcrosscorrelation(ShotNo,'rp_4','rp_4',5000,5000)    # just to develop
    

In [3]:
# Basic graph generation
def BasicGraph(ShotNo, signal1, signal2, axvspan_start,axvspan_end):

    def axvspan():
        plt.axvspan(PlasmaStart/1000+axvspan_start, PlasmaStart/1000+axvspan_end, facecolor='0.5', alpha=0.5)


    fig = plt.figure(1)
    subplots_adjust(hspace=0.001)

    sbp1=plt.subplot(711)
    data1 = GMgetdata_txt(ShotNo,'loop_voltage')
    plt.ylim(0,max(data1[:,1]*1.1))
    plt.yticks(arange(0, 30, 10))
    plt.title('#'+str(ShotNo)+ '..<'+str(int(PlasmaStart+axvspan_start*1000))+','+str(int(PlasmaStart+axvspan_end*1000))+'>')
    plt.ylabel('$U_l$ [V]')
    plt.plot(data1[:,0]*1000, data1[:,1], 'k-',label='Loop voltage $U_l$' )
    plt.legend(loc=0)
    axvspan()

    sbp1=plt.subplot(712, sharex=sbp1)
    data2 = GMgetdata_txt(ShotNo,'toroidal_field')
    plt.yticks(arange(0, 0.5 , 0.2))
    plt.ylim(0,max(data2[:,1]*1.1))
    plt.ylabel('$B_t$ [T]')
    plt.plot(data2[:,0]*1000, data2[:,1], 'k-',label='Toroidal mag. field $B_t$')
    plt.legend(loc=0)
    axvspan()

    sbp1=plt.subplot(713, sharex=sbp1)
    data3 = GMgetdata_txt(ShotNo,'plasma_current')
    plt.yticks(arange(0,max(data3[:,1]/1000), 0.5))
    plt.ylim(0,max(data3[:,1]/1000*1.1))
    plt.ylabel('$I_p$ [kA]')
    plt.plot(data3[:,0]*1000, data3[:,1]/1000, 'k-',label='Plasma current $I_p$')
    plt.legend(loc=0)
    axvspan()

    sbp1=plt.subplot(714, sharex=sbp1)
    data4 = GMgetdata_txt(ShotNo,'photodiode_alpha')
    plt.yticks(arange(0, 0.09 , 0.03))
    #plt.ylim(0,max(data4[:,1]*1.1))
    plt.ylim(0,0.09)
    plt.ylabel('I [a.u.]')
    plt.plot(data4[:,0]*1000, data4[:,1], 'k-',label='$H_\\alpha$ radiation')
    plt.legend(loc=0)
    axvspan()

    sbp1=plt.subplot(715, sharex=sbp1)
    data5 = GMgetdata_identifier(ShotNo,'electron_density')
    #plt.yticks(arange(0, max(data5[:,1]), 0.5))
    #plt.ylim(0,0.8)
    plt.ylabel('$n_e$')
    plt.plot(data5[:,0]*1000, data5[:,1], 'k-',label='electron density $n_e$')
    plt.legend(loc=0)
    axvspan()
    
    sbp1=plt.subplot(716, sharex=sbp1)
    data6 = GMgetdata_txt(ShotNo,signal1)
    plt.ylim(min(data6[PlasmaStart:PlasmaEnd,1]),max(data6[PlasmaStart:PlasmaEnd,1]))
    plt.ylabel('U [V]')
    plt.plot(data6[:,0]*1000, data6[:,1], 'k-',label=signal1)
    plt.legend(loc=0)
    axvspan()
    
    sbp1=plt.subplot(717, sharex=sbp1)
    data7 = GMgetdata_txt(ShotNo,signal2)
    plt.ylim(min(data7[PlasmaStart:PlasmaEnd,1]),max(data7[PlasmaStart:PlasmaEnd,1]))
    plt.ylabel('U [V]')
    plt.xticks(arange(int(PlasmaStart/1000),int(PlasmaEnd/1000), 2))
    plt.xlim(PlasmaStart/1000*0.9,PlasmaEnd/1000*1.1)
    plt.xlabel('Time [ms]')
    plt.plot(data7[:,0]*1000, data7[:,1], 'k-',label=signal2)
    plt.legend(loc=0)
    axvspan()

    xticklabels = sbp1.get_xticklabels()
    plt.setp(xticklabels, visible=True)
    
    
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/'+str(int(axvspan_start*1000))+'to'+str(int(axvspan_end*1000))+'basic.jpg')

    
    #plt.show()

#BasicGraph(26360,'rp_4','rp_10',8,9)

    

In [4]:
def htmlgeneration(ShotNo,signal1,signal2,PlasmaStart,PlasmaEnd,step):
    
    print("html generation ...")
    ShotNoStr=str(ShotNo)

    os.system('rm CrossCorrels/'+signal1+'x'+signal2+'/index.html');
    fileid = open('CrossCorrels/'+signal1+'x'+signal2+'/index.html','a+')
    fileid.write('<html><head><title>VA char @ GOLEM</title>\
    <style>\
    div.grafy30 {display:inline-block;width: 30%;}\
    div.grafy20 {display:inline-block;width: 20%;}\
    .grafy20 img {width: 100%;}\
    .grafy30 img {width: 100%;}\
    </style>\
    <meta http-equiv="Content-Type" content="text/html; charset=utf-8">\
    <style></style>\
    <script type="text/x-mathjax-config">MathJax.Hub.Config({tex2jax: {inlineMath: [[\'$\',\'$\'], [\'\\(\',\'\\)\']]}});</script>\
    <script src="https://cdn.mathjax.org/mathjax/latest/MathJax.js?config=TeX-AMS-MML_HTMLorMML"></script>\
    </head><body><center>')
    fileid.write('<h2><a href="../../index.html">Home</a></h2>')
    fileid.write('<h1>He experiments @ the GOLEM tokamak</h1>')
    fileid.write('<h2>Cross-correlation analysis between <b>'+signal1+' &amp; '+signal2+' signals with '+str(step)+' us @ #'+ShotNoStr+'</b></h2>')
    fileid.write('<h3>Essential parameters:</h3><table><tr><td><ul>\
    <li>Voltage divider: 1:'+str(HWNapetovyDelic)+'</li>\
    <li>The shot: <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'">'+ShotNoStr+'</a></li>\
    <li>The DAS used: <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'/DAS/1011Papouch_St.ON/">Papouch_St</a></li>'+\
    '<li>Date:'+ GMget_str_parameter(ShotNo,"time")+'@'+GMget_str_parameter(ShotNo,"date")+'</li>'+\
    '</ul></td></tr></table>')
    fileid.write('<div class="grafy30"><h2>The discharge #'+ShotNoStr+'</h2>')
    fileid.write('<h3>Basic diagnostics</h3>\
    <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'/"><img src="../../Data/graphres.png" width="100%"></a><br/>\
    Plasma start:<a href="ShotNo/PlasmaStart">'+str(PlasmaStart)+'</a> us\
    Plasma end:<a href="ShotNo/PlasmaEnd">'+str(PlasmaEnd)+'</a> us</div>')
    fileid.write('<br/><table><tr><td><img src="CrossCoefsTimes.jpg"><br/><a href="CorrCoefsTimes">Correlation coefficients</a></td><td><img src="CrossCoefsValues.jpg"><br/><a href="CorrCoefsValue">Correlation coefficients values</a></td></tr></table>')
    fileid.write('<table border="1">\
    <tr><th>Basic diagnostics</th><th>Raw correlated signals</th><th>Full correlation</th><th>Full correlation - zoom</th></tr>')
    for i in range(0, PlasmaEnd-PlasmaStart, step):
        fileid.write('\
        <td><img src="'+str(i)+'to'+str((i+step))+'basic.jpg"></td>\
        <td><img src="'+str(i)+'to'+str((i+step))+'raw-mean.jpg"><br/><center><a href="'+str(i)+'to'+str((i+step))+signal1+'raw.dat">'+signal1+' (raw)</a> .. <a href="'+str(i)+'to'+str((i+step))+signal2+'raw.dat">'+signal2+' (raw)</a> from '+str(PlasmaStart+i)+' to '+str((PlasmaStart+i+step))+' us<br/><center><a href="'+str(i)+'to'+str((i+step))+signal1+'raw-mean.dat">'+signal1+' (raw-mean)</a> .. <a href="'+str(i)+'to'+str((i+step))+signal2+'raw-mean.dat">'+signal2+' (raw-mean)</a> from '+str(PlasmaStart+i)+' to '+str((PlasmaStart+i+step))+' us  </center></td>\
        <td><img src="'+str(i)+'to'+str((i+step))+'.jpg"><br/><center><a href="'+str(i)+'to'+str((i+step))+'.dat">Correlation</a> from '+str(PlasmaStart+i)+' to '+str((PlasmaStart+i+step))+' us </center></td>\
        <td><img src="'+str(i)+'to'+str((i+step))+'z.jpg"></td>\
        </tr>')
    fileid.write('\
    <td><img src="moviebasic.gif"></td>\
    <td><img src="movieraw.gif"></td>\
    <td><img src="movie.gif"></td>\
    <td><img src="moviez.gif"></td>\
    </table>') 
    fileid.write('</body></html>')
 
    
#htmlgeneration(ShotNo,'rp_4','rp_4',PlasmaStart,PlasmaEnd,step) # just to develop 


In [5]:
def globalhtmlgeneration():
    
    print("global html generation ...")
    ShotNoStr=str(ShotNo)

    os.system('rm index.html');
    fileid = open('index.html','a+')
    fileid.write('<html><head><title>VA char @ GOLEM</title>\
    <style>\
    div.grafy30 {display:inline-block;width: 30%;}\
    div.grafy20 {display:inline-block;width: 20%;}\
    .grafy20 img {width: 100%;}\
    .grafy30 img {width: 100%;}\
    </style>\
    <meta http-equiv="Content-Type" content="text/html; charset=utf-8">\
    <style></style>\
    <script type="text/x-mathjax-config">MathJax.Hub.Config({tex2jax: {inlineMath: [[\'$\',\'$\'], [\'\\(\',\'\\)\']]}});</script>\
    <script src="https://cdn.mathjax.org/mathjax/latest/MathJax.js?config=TeX-AMS-MML_HTMLorMML"></script>\
    </head><body><center>')
    fileid.write('<h1>He experiments @ the GOLEM tokamak</h1>')
    fileid.write('<h2>Cross-correlation analysis of signals:</b></h2>')
    for signal1 in Signals:
        fileid.write(signal1+',')
    fileid.write('@ '+str(step)+' us<h3>Essential parameters:</h3><table><tr><td><ul>\
    <li>Voltage divider: 1:'+str(HWNapetovyDelic)+'</li>\
    <li>The shot: <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'">'+ShotNoStr+'</a></li>\
    <li>The DAS used: <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'/DAS/1011Papouch_St.ON/">Papouch_St</a></li>'+\
    '<li>Date:'+ GMget_str_parameter(ShotNo,"time")+'@'+GMget_str_parameter(ShotNo,"date")+'</li>'+\
    '</ul></td></tr></table>')
    fileid.write('<div class="grafy30"><h2>The discharge #'+ShotNoStr+'</h2>')
    fileid.write('<h3>Basic diagnostics</h3>\
    <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'/"><img src="Data/graphres.png" width="100%"></a><br/>\
    Plasma start:<a href="ShotNo/PlasmaStart">'+str(PlasmaStart)+'</a> us\
    Plasma end:<a href="ShotNo/PlasmaEnd">'+str(PlasmaEnd)+'</a> us</div>')
    fileid.write('<h3><a href="CrossCorrelMaps/index.html">Cross correlation analysis</h3>\
    <a href="http://golem.fjfi.cvut.cz/shots/'+ShotNoStr+'/"><img src="CrossCorrels/drp2xdrp2/moviebasic.gif" width="30%"></a>\
    <a href="CrossCorrelMaps/index.html"><img src="CrossCorrelMaps/450to550/movie.gif" width="30%"></a>')
    fileid.write('<table border="1">\
    <tr><th>Signal identification</th><th>Basic diagnostics</th><th>Raw correlated signals</th><th>Full correlation</th><th>Full correlation - zoom</th><th>Cross-corel:times</th><th>Cross-corel:values</th></tr>')
    for signaly in combinations_with_replacement(Signals, 2):
        signal1=signaly[0];signal2=signaly[1]
        fileid.write('<tr>\
        <td><a href="CrossCorrels/'+signal1+'x'+signal2+'/index.html"><img src="CrossCorrels/'+signal1+'x'+signal2+'/signalfig.png"></a></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/moviebasic.gif"></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/movieraw.gif"></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/movie.gif"></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/moviez.gif"></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/CrossCoefsTimes.jpg"></td>\
        <td><img src="CrossCorrels/'+signal1+'x'+signal2+'/CrossCoefsValues.jpg"></td>')
    fileid.write('</tr></table>\
    <a href="Analysis.ipynb">ipynb creator</a> ... <a href="Analysis.html">ipynb creator (html)</a><br/>\
    <a href="http://golem.fjfi.cvut.cz/wikiraw/Handling/CompAlgSystems4Golem/jupyter-python/Sandbox/0418CrossCorrelation/Analysis.html">Cross correlation sandbox (numpy.correlate tests)</a>\
    </body></html>')
 
    
# globalhtmlgeneration()  # just to tune it ..

In [6]:
# Crosscorrealation issues
def ccormap(basesignal, startT, finalT, startDelay, finalDelay):
    ccorpath=os.getcwd()
    mkdir(ccorpath+'/CrossCorrelMaps/'+str(startDelay)+'to'+str(finalDelay))
    CorrCoefsMap=np.empty((0, finalDelay-startDelay))
    for signal in Signals:
        #print(signal)
        CorrCoefsMap=append(CorrCoefsMap,[np.loadtxt(ccorpath+'/CrossCorrels/'+basesignal+'x'+signal+'/'+str(startT)+'to'+str(finalT)+'.dat')[startDelay:finalDelay]], axis=0)
    plt.imshow(CorrCoefsMap,aspect='auto',extent = [-(finalDelay-startDelay)/2,(finalDelay-startDelay)/2,0, 7.5],
               interpolation='bicubic',cmap=plt.cm.hot, vmax=1, vmin=-0.5)
    plt.title('t=<'+str(PlasmaStart+startT)+','+str(PlasmaStart+finalT)+'> us' )
    plt.xlabel('Delay [us]')
    plt.ylabel('z [mm]')
    plt.colorbar()
    plt.savefig(ccorpath+'/CrossCorrelMaps/'+str(startDelay)+'to'+str(finalDelay)+'/'+str(startT)+'to'+str(finalT)+'.jpg', bbox_inches='tight')
    #plt.show()
    plt.clf()
    with open(ccorpath+'/CrossCorrelMaps/'+str(startDelay)+'to'+str(finalDelay)+'/sequence', "a+") as text_file: 
        text_file.write(str(startT)+'to'+str(finalT)+'.jpg\n')
    np.savetxt(ccorpath+'/CrossCorrelMaps/'+str(startDelay)+'to'+str(finalDelay)+'/data',CorrCoefsMap, delimiter=" ", fmt="%s")    

def ccormapgeneration():    
    ccorpath=os.getcwd()    
    mkdir(ccorpath+'/CrossCorrelMaps/')
    os.system('rm '+ccorpath+'/CrossCorrelMaps/index.html');
    fileid = open(ccorpath+'/CrossCorrelMaps/index.html','a+')
    fileid.write('<html><head><title>VA char @ GOLEM</title><style>\
        div.grafy100 {display:inline-block;width: 100%;}\
        div.grafy50 {display:inline-block;width: 50%;}\
        div.grafy30 {display:inline-block;width: 30%;}\
        div.grafy20 {display:inline-block;width: 20%;}\
        .grafy100 img {width: 100%;}\
        .grafy50 img {width: 100%;}\
        .grafy20 img {width: 100%;}\
        .grafy30 img {width: 100%;}\
        </style>\</head><body><center>')
    fileid.write('<h1>He experiments @ the GOLEM tokamak</h1>')
    fileid.write('<h2>Cross-correlation analysis of signals:</b></h2><div class="grafy100">')
    fileid.write('<table><tr><th width="25%"></th><th width="25%"></th><th width="25%"></th><th width="25%"></th></tr>')
    finalTime=11000; TimeShift=step
    for TimeDelay in [1,999], [400,600], [450,550]:
        os.system('rm '+ccorpath+'/CrossCorrelMaps/'+str(TimeDelay[0])+'to'+str(TimeDelay[1])+'/sequence')
        for i in range(0, finalTime, TimeShift): 
            ccormap(Signals[0],i,i+TimeShift, TimeDelay[0], TimeDelay[1])
        os.system('cd '+ccorpath+'/CrossCorrelMaps/'+str(TimeDelay[0])+'to'+str(TimeDelay[1])+';convert -delay 100 @sequence movie.gif')
    for i in range(0, finalTime, TimeShift):    
        fileid.write('<tr>\
        <td><img src=../CrossCorrels/'+Signals[0]+'x'+Signals[0]+'/'+str(i)+'to'+str(i+TimeShift)+'basic.jpg></td>\
        <td><center><img src='+str(1)+'to'+str(999)+'/'+str(i)+'to'+str(i+TimeShift)+'.jpg><br/><a href='+str(1)+'to'+str(999)+'/data>data</a></center></td>\
        <td><center><img src='+str(400)+'to'+str(600)+'/'+str(i)+'to'+str(i+TimeShift)+'.jpg><br/><a href='+str(400)+'to'+str(600)+'/data>data</a></center></td>\
        <td><center><img src='+str(450)+'to'+str(550)+'/'+str(i)+'to'+str(i+TimeShift)+'.jpg><br/><a href='+str(450)+'to'+str(550)+'/data>data</a></center></td>\
        </tr>')
        print(i)
    fileid.write('<tr>\
    <td><img src=../CrossCorrels/'+Signals[0]+'x'+Signals[0]+'/moviebasic.gif></td>\
    <td><img src='+str(1)+'to'+str(999)+'/movie.gif></td>\
    <td><img src='+str(400)+'to'+str(600)+'/movie.gif></td>\
    <td><img src='+str(450)+'to'+str(550)+'/movie.gif></td>\
    </tr>')
    fileid.write('</div></table></body></html>')    
    fileid.close()


In [7]:
# main    
    
GetData(ShotNo)

for signaly in combinations_with_replacement(Signals, 2):
    signal1=signaly[0];signal2=signaly[1]
    print()
    print(signal1+' '+signal2);
    mkdir('CrossCorrels/'+signal1+'x'+signal2)
    CorrCoefs=[];TimeSequence=[];CorrCoefsTime=[];CorrCoefsValue=[];j=0
    for i in range(0, PlasmaEnd-PlasmaStart, step):
        print(i, end=',')
        CorrCoefs.append([i/1000,GMcrosscorrelation(ShotNo,signal1,signal2,i,i+step)])
        CorrCoefsTime.append([i/1000,CorrCoefs[j][1][0]])
        CorrCoefsValue.append([i/1000,CorrCoefs[j][1][1]])
        BasicGraph(str(ShotNo),signal1,signal2,i/1000,(i+step)/1000)
        os.system('convert -size 240x120 xc:White -gravity Center -weight 700 -pointsize 25 -font "Times-Roman" -annotate 0 "'+signal1+'\nx\n'+signal2+'\n\n(click)'+'" CrossCorrels/'+signal1+'x'+signal2+'/signalfig.png')
        TimeSequence.append([str(i)+'to'+str(i+step)])
        j=j+1
    np.savetxt('TimeSequence',TimeSequence, delimiter=" ", fmt="%s")
    plt.clf()
    plt.ylim(step*0.95, step*1.05)
    plt.title('')
    plt.xlabel('Time [ms]')
    plt.ylabel('Cross-correlation coef.')
    plt.plot(np.array(CorrCoefsTime)[:,0],np.array(CorrCoefsTime)[:,1],"*")
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/CrossCoefsTimes.jpg', bbox_inches='tight')
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/CorrCoefsTimes',CorrCoefsTime, delimiter=" ", fmt="%s")
    plt.clf()
    plt.ylim(0, 1.05)
    plt.title('')
    plt.xlabel('Time [ms]')
    plt.ylabel('Cross-correlation coef. vals')
    plt.plot(np.array(CorrCoefsValue)[:,0],np.array(CorrCoefsValue)[:,1],"*")
    plt.savefig('CrossCorrels/'+signal1+'x'+signal2+'/CrossCoefsValues.jpg', bbox_inches='tight')
    os.system('cd CrossCorrels/'+signal1+'x'+signal2+'/;cp ../../../moviescript.bash .;bash moviescript.bash')
    np.savetxt('CrossCorrels/'+signal1+'x'+signal2+'/CorrCoefsValue',CorrCoefsValue, delimiter=" ", fmt="%s")
    htmlgeneration(ShotNo,signal1,signal2,PlasmaStart,PlasmaEnd,step)    
    np.savetxt('TimeSequence',TimeSequence, delimiter=" ", fmt="%s")
    #plt.show()
    globalhtmlgeneration()
    ccormapgeneration()
    



drp2 drp2
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000,10500,11000,11500,html generation ...
global html generation ...

drp2 drp4
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000,10500,11000,11500,html generation ...
global html generation ...

drp2 drp6
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000,10500,11000,11500,html generation ...
global html generation ...

drp2 drp8
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000,10500,11000,11500,html generation ...
global html generation ...

drp4 drp4
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000,10500,11000,11500,html generation ...
global html generation ...

drp4 drp6
0,500,1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,100

In [8]:
ccormapgeneration()

0
500
1000
1500
2000
2500
3000
3500
4000
4500
5000
5500
6000
6500
7000
7500
8000
8500
9000
9500
10000
10500
